<a href="https://colab.research.google.com/github/shivamdhumal77/LLM_Projects/blob/main/llm_sound_1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install torch
!pip install git+https://github.com/openai/whisper.git
!pip install parler-tts
!pip install transformers
!pip install langchain-community
!pip install soundfile
 # If you want to test audio playback functionality, though note it's not ideal for Colab.


  Cloning https://github.com/openai/whisper.git to /tmp/pip-req-build-lyjnst_w
  Running command git clone --filter=blob:none --quiet https://github.com/openai/whisper.git /tmp/pip-req-build-lyjnst_w
  Resolved https://github.com/openai/whisper.git to commit 90db0de1896c23cbfaf0c58bc2d30665f709f170
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 209.5/209.5 MB 5.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 59.9 MB/s eta 0:00:00
  Created wheel for openai-whisper: filename=openai_whisper-20240930-py3-none-any.whl size=803583 sha256=d0faad52d9ba81bc39d4aadd320c7db685ed42753bbe3c797a599da79af9b040
  Stored in directory: /tmp/pip-ephem-wheel-cache-an8y4h9m/wheels/8b/6c/d0/622666868c179f156cf595c8b6f06f88bc5d80c4b31dccaa03
Successfully built openai-whisper
ERROR: Could not find a version that satisfies the requirement parler-tts (fro

In [2]:
pip install git+https://github.com/huggingface/parler-tts.git

  Cloning https://github.com/huggingface/parler-tts.git to /tmp/pip-req-build-_ujiptk0
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/parler-tts.git /tmp/pip-req-build-_ujiptk0
  Resolved https://github.com/huggingface/parler-tts.git to commit d108732cd57788ec86bc857d99a6cabd66663d68
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Cloning https://github.com/descriptinc/audiotools to /tmp/pip-install-ol7e6ymn/descript-audiotools_51dc5ce37ed9440cb9a41851d24a3df2
  Running command git clone --filter=blob:none --quiet https://github.com/descriptinc/audiotools /tmp/pip-install-ol7e6ymn/descript-audiotools_51dc5ce37ed9440cb9a41851d24a3df2
  Resolved https://github.com/descriptinc/audiotools to commit 348ebf2034ce24e2a91a553e3171cb00c0c71678
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.1/44.1 kB 4.0 MB/s eta 0:00:00
  Prep

In [ ]:
pip install colab-xterm

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.6/115.6 kB 3.3 MB/s eta 0:00:00


In [ ]:
%load_ext colabxterm

In [ ]:
# put this in the terminal and follow these steps
#curl https://ollama.ai/install.sh | sh
# ollama serve & ollama pull llama3.2
%xterm

Launching Xterm...

<IPython.core.display.Javascript object>

In [ ]:
%xterm

Launching Xterm...

<IPython.core.display.Javascript object>

In [ ]:
pip install ollama

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.4/76.4 kB 4.7 MB/s eta 0:00:00
  Attempting uninstall: httpx
    Found existing installation: httpx 0.28.1
    Uninstalling httpx-0.28.1:
      Successfully uninstalled httpx-0.28.1


In [ ]:
%xterm

Launching Xterm...

<IPython.core.display.Javascript object>

In [ ]:
import whisper
import torch
from parler_tts import ParlerTTSForConditionalGeneration
from transformers import AutoTokenizer, set_seed
import numpy as np
from langchain_community.llms.ollama import Ollama
import soundfile as sf
from IPython.display import Audio

# Initialize Whisper model for transcription
whisper_model = whisper.load_model("tiny")  # Use 'tiny' for faster transcription

# Initialize ParlerTTS for speech synthesis
device = "cuda:0" if torch.cuda.is_available() else "cpu"
model_name = "parler-tts/parler-tts-mini-v1"  # Adjust this model name as needed
tts_model = ParlerTTSForConditionalGeneration.from_pretrained(model_name).to(device)
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Initialize Ollama for text-based response generation
ollama = Ollama(model="llama3.2")

# Function for transcribing uploaded audio file using Whisper
def transcribe_from_audio(file_path):
    audio = whisper.load_audio(file_path)
    audio = whisper.pad_or_trim(audio)
    mel = whisper.log_mel_spectrogram(audio).to(device)

    options = whisper.DecodingOptions(fp16=False)
    result = whisper.decode(whisper_model, mel, options)
    return result.text

# Function for generating a response from Ollama
def generate_response(user_input):
    print(f"User: {user_input}")
    response = ollama(user_input)
    response_text = response.strip()  # Clean up the response
    print(f"Ollama: {response_text}")
    return response_text

# Function to synthesize speech using ParlerTTS
def synthesize_speech(text, voice_description):
    input_ids = tokenizer(voice_description, return_tensors="pt").input_ids.to(device)
    prompt_input_ids = tokenizer(text, return_tensors="pt").input_ids.to(device)
    generation = tts_model.generate(input_ids=input_ids, prompt_input_ids=prompt_input_ids)
    audio_arr = generation.cpu().numpy().squeeze()
    return audio_arr

# Function to play audio using Colab's native player
def play_audio(audio_array, sample_rate=22050):
    sf.write("synthesized_audio.wav", audio_array, sample_rate)  # Save audio to a .wav file
    return Audio("synthesized_audio.wav", autoplay=True)  # Return an Audio object for playback in Colab

# Main function for simulating the conversation
def conversation(file_path):
    voice_description = "A female speaker delivers a slightly expressive and animated speech with a moderate speed and pitch. The recording is of very high quality, with the speaker's voice sounding clear and very close up"

    # Step 1: Transcribe user input from the uploaded audio file
    user_input = transcribe_from_audio(file_path)

    # Step 2: Generate a response using Ollama
    response = generate_response(user_input)

    # Step 3: Synthesize response into speech
    audio = synthesize_speech(response, voice_description)

    # Step 4: Play synthesized speech
    return play_audio(audio)


# Upload an audio file manually in Colab, e.g., using this code snippet:
from google.colab import files
uploaded = files.upload()

# Choose the first uploaded file to use for transcription
file_path = list(uploaded.keys())[0]

# Run the conversation (transcription, response generation, and playback)
conversation(file_path)



100%|█████████████████████████████████████| 72.1M/72.1M [00:00<00:00, 90.6MiB/s]
/usr/local/lib/python3.10/dist-packages/whisper/__init__.py:150: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this exper

config.json:   0%|          | 0.00/6.93k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/3.51G [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/torch/nn/utils/weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)
  "_name_or_path": "google/flan-t5-large",
  "architectures": [
    "T5ForConditionalGeneration"
  ],
  "classifier_dropout": 0.0,
  "d_ff": 2816,
  "d_kv": 64,
  "d_model": 1024,
  "decoder_start_token_id": 0,
  "dense_act_fn": "gelu_new",
  "dropout_rate": 0.1,
  "eos_token_id": 1,
  "feed_forward_proj": "gated-gelu",
  "initializer_factor": 1.0,
  "is_encoder_decoder": true,
  "is_gated_act": true,
  "layer_norm_epsilon": 1e-06,
  "model_type": "t5",
  "n_positions": 512,
  "num_decoder_layers": 24,
  "num_heads": 16,
  "num_layers": 24,
  "output_past": true,
  "pad_token_id": 0,
  "relative_attention_max_distance": 128,
  "relative_attention_num_buckets": 32,
  "tie_word_embeddings": false,
  "transformers_version": "4.46.1",
  "use_cache": true,
  "vocab

generation_config.json:   0%|          | 0.00/265 [00:00<?, ?B/s]

...

special_tokens_map.json:   0%|          | 0.00/2.54k [00:00<?, ?B/s]

<ipython-input-9-1e99853646e4>:20: LangChainDeprecationWarning: The class `Ollama` was deprecated in LangChain 0.3.1 and will be removed in 1.0.0. An updated version of the class exists in the :class:`~langchain-ollama package and should be used instead. To use it run `pip install -U :class:`~langchain-ollama` and import as `from :class:`~langchain_ollama import OllamaLLM``.
  ollama = Ollama(model="llama3.2")


Saving #3.wav to #3.wav
User: Because if there is one word to describe me, I'm a 5th. It is in my genes. I am my parents. So let me start from the very beginning. My father.


<ipython-input-9-1e99853646e4>:35: LangChainDeprecationWarning: The method `BaseLLM.__call__` was deprecated in langchain-core 0.1.7 and will be removed in 1.0. Use :meth:`~invoke` instead.
  response = ollama(user_input)
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


Ollama: It sounds like you're looking to explore your family heritage and see how it influences who you are today.

Let's start with your father. You mentioned that being a 5th is "in my genes" - do you mean that you have a surname or family name that is common in certain families, but not as commonly found elsewhere?

If so, I'd love to help you explore this connection and see how it might be reflected in your personality or traits. Or if you'd like to share more about what being a 5th means to you, I'm all ears!


In [ ]:
import torch
from parler_tts import ParlerTTSForConditionalGeneration
from transformers import AutoTokenizer
import soundfile as sf

# Set up the ParlerTTS model and tokenizer
device = "cuda:0" if torch.cuda.is_available() else "cpu"
model = ParlerTTSForConditionalGeneration.from_pretrained("parler-tts/parler-tts-mini-v1").to(device)
tokenizer = AutoTokenizer.from_pretrained("parler-tts/parler-tts-mini-v1")

# Text to synthesize (generated response from Snippet 1)
prompt = "Generated text from Snippet 1"
description = "A female speaker delivers a slightly expressive and with a moderate speed and pitch. The recording is of very high quality, with the speaker's voice sounding clear and very close up."

# Prepare input for the model
input_ids = tokenizer(description, return_tensors="pt").input_ids.to(device)
prompt_input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

# Generate audio using ParlerTTS
generation = model.generate(input_ids=input_ids, prompt_input_ids=prompt_input_ids)
audio_arr = generation.cpu().numpy().squeeze()

# Save synthesized speech to a file
sf.write("parler_tts_out.wav", audio_arr, model.config.sampling_rate)
print("Speech synthesis complete. File saved as 'parler_tts_out.wav'")


/usr/local/lib/python3.10/dist-packages/torch/nn/utils/weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)
  "_name_or_path": "google/flan-t5-large",
  "architectures": [
    "T5ForConditionalGeneration"
  ],
  "classifier_dropout": 0.0,
  "d_ff": 2816,
  "d_kv": 64,
  "d_model": 1024,
  "decoder_start_token_id": 0,
  "dense_act_fn": "gelu_new",
  "dropout_rate": 0.1,
  "eos_token_id": 1,
  "feed_forward_proj": "gated-gelu",
  "initializer_factor": 1.0,
  "is_encoder_decoder": true,
  "is_gated_act": true,
  "layer_norm_epsilon": 1e-06,
  "model_type": "t5",
  "n_positions": 512,
  "num_decoder_layers": 24,
  "num_heads": 16,
  "num_layers": 24,
  "output_past": true,
  "pad_token_id": 0,
  "relative_attention_max_distance": 128,
  "relative_attention_num_buckets": 32,
  "tie_word_embeddings": false,
  "transformers_version": "4.46.1",
  "use_cache": true,
  "vocab

In [ ]:
import whisper
import torch
from langchain_community.llms.ollama import Ollama

# Initialize Whisper model for transcription
whisper_model = whisper.load_model("tiny")  # Use 'tiny' for faster transcription

# Initialize Ollama for text-based response generation
ollama = Ollama(model="llama3.2")

# Function for transcribing uploaded audio file using Whisper
def transcribe_from_audio(file_path):
    audio = whisper.load_audio(file_path)
    audio = whisper.pad_or_trim(audio)
    mel = whisper.log_mel_spectrogram(audio).to("cpu")  # Device set to CPU for compatibility

    options = whisper.DecodingOptions(fp16=False)
    result = whisper.decode(whisper_model, mel, options)
    return result.text

# Function for generating a response from Ollama
def generate_response(user_input):
    print(f"User: {user_input}")
    response = ollama(user_input)
    response_text = response.strip()  # Clean up the response
    print(f"Ollama: {response_text}")
    return response_text

# Main function for transcription and response
def process_audio(file_path):
    # Step 1: Transcribe user input from the uploaded audio file
    user_input = transcribe_from_audio(file_path)

    # Step 2: Generate a response using Ollama
    response = generate_response(user_input)

    return response

# Upload an audio file manually in Colab
from google.colab import files
uploaded = files.upload()

# Choose the first uploaded file to use for transcription
file_path = list(uploaded.keys())[0]

# Run transcription and response generation
response_text = process_audio(file_path)
print(f"Generated Response: {response_text}")


In [ ]:
import torch
from parler_tts import ParlerTTSForConditionalGeneration
from transformers import AutoTokenizer
import soundfile as sf

# Set up the ParlerTTS model and tokenizer
device = "cuda:0" if torch.cuda.is_available() else "cpu"
model = ParlerTTSForConditionalGeneration.from_pretrained("parler-tts/parler-tts-mini-v1").to(device)
tokenizer = AutoTokenizer.from_pretrained("parler-tts/parler-tts-mini-v1")

# Text to synthesize (generated response from Snippet 1)
prompt = "Generated text from Snippet 1"
description = "A female speaker delivers a slightly expressive and with a moderate speed and pitch. The recording is of very high quality, with the speaker's voice sounding clear and very close up."

# Prepare input for the model
input_ids = tokenizer(description, return_tensors="pt").input_ids.to(device)
prompt_input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

# Generate audio using ParlerTTS
generation = model.generate(input_ids=input_ids, prompt_input_ids=prompt_input_ids)
audio_arr = generation.cpu().numpy().squeeze()

# Save synthesized speech to a file
sf.write("parler_tts_out.wav", audio_arr, model.config.sampling_rate)
print("Speech synthesis complete. File saved as 'parler_tts_out.wav'")


In [1]:
!pip install fastapi uvicorn pydantic torch transformers soundfile


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 94.8/94.8 kB 8.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.3/62.3 kB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.2/73.2 kB 7.0 MB/s eta 0:00:00


In [3]:
pip install git+https://github.com/huggingface/parler-tts.git

  Cloning https://github.com/huggingface/parler-tts.git to /tmp/pip-req-build-9mwmwz8r
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/parler-tts.git /tmp/pip-req-build-9mwmwz8r
  Resolved https://github.com/huggingface/parler-tts.git to commit d108732cd57788ec86bc857d99a6cabd66663d68
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Cloning https://github.com/descriptinc/audiotools to /tmp/pip-install-que4y18z/descript-audiotools_6b8ab2d3da9947b9acf7c5e2e10bd97e
  Running command git clone --filter=blob:none --quiet https://github.com/descriptinc/audiotools /tmp/pip-install-que4y18z/descript-audiotools_6b8ab2d3da9947b9acf7c5e2e10bd97e
  Resolved https://github.com/descriptinc/audiotools to commit 348ebf2034ce24e2a91a553e3171cb00c0c71678
  Preparing metadata (setup.py) ... done


In [ ]:
from fastapi import FastAPI
from pydantic import BaseModel
import torch
from parler_tts import ParlerTTSForConditionalGeneration
from transformers import AutoTokenizer
import soundfile as sf
from io import BytesIO
import nest_asyncio
import uvicorn

# Set the device to GPU if available
device = "cuda:0" if torch.cuda.is_available() else "cpu"

# Initialize FastAPI app
app = FastAPI()

# Load Parler TTS model and tokenizer
model = ParlerTTSForConditionalGeneration.from_pretrained("parler-tts/parler-tts-mini-v1").to(device)
tokenizer = AutoTokenizer.from_pretrained("parler-tts/parler-tts-mini-v1")

# Define the request body structure
class TextRequest(BaseModel):
    prompt: str
    description: str

@app.post("/generate_speech/")
async def generate_speech(request: TextRequest):
    prompt = request.prompt
    description = request.description

    # Tokenize the input description and prompt
    input_ids = tokenizer(description, return_tensors="pt").input_ids.to(device)
    prompt_input_ids = tokenizer(prompt, return_tensors="pt").input_ids.to(device)

    # Generate the speech using ParlerTTS model
    generation = model.generate(input_ids=input_ids, prompt_input_ids=prompt_input_ids)
    audio_arr = generation.cpu().numpy().squeeze()

    # Save audio to a buffer
    audio_io = BytesIO()
    sf.write(audio_io, audio_arr, model.config.sampling_rate, format='WAV')
    audio_io.seek(0)

    # Return the audio in binary format as a response
    return {"audio": audio_io.getvalue()}

# Use nest_asyncio to run the FastAPI server in Colab
nest_asyncio.apply()

# Start the server
uvicorn.run(app, host="0.0.0.0", port=8000)


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/6.93k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/3.51G [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/torch/nn/utils/weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)
  "_name_or_path": "google/flan-t5-large",
  "architectures": [
    "T5ForConditionalGeneration"
  ],
  "classifier_dropout": 0.0,
  "d_ff": 2816,
  "d_kv": 64,
  "d_model": 1024,
  "decoder_start_token_id": 0,
  "dense_act_fn": "gelu_new",
  "dropout_rate": 0.1,
  "eos_token_id": 1,
  "feed_forward_proj": "gated-gelu",
  "initializer_factor": 1.0,
  "is_encoder_decoder": true,
  "is_gated_act": true,
  "layer_norm_epsilon": 1e-06,
  "model_type": "t5",
  "n_positions": 512,
  "num_decoder_layers": 24,
  "num_heads": 16,
  "num_layers": 24,
  "output_past": true,
  "pad_token_id": 0,
  "relative_attention_max_distance": 128,
  "relative_attention_num_buckets": 32,
  "tie_word_embeddings": false,
  "transformers_version": "4.46.1",
  "use_cache": true,
  "vocab

generation_config.json:   0%|          | 0.00/265 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/20.8k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.42M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.54k [00:00<?, ?B/s]

INFO:     Started server process [1566]
INFO:     Waiting for application startup.
INFO:     Application startup complete.
INFO:     Uvicorn running on http://0.0.0.0:8000 (Press CTRL+C to quit)


In [ ]:
import requests

# Define the API endpoint
url = "http://127.0.0.1:8000/generate_speech/"

# Define the payload
payload = {
    "prompt": "Let's talk about the importance of technology.",
    "description": "Technology has revolutionized every aspect of our lives, from communication to healthcare."
}

# Send the POST request
response = requests.post(url, json=payload)

# Check the response
if response.status_code == 200:
    audio_data = response.json()["audio"]

    # Save the audio file
    with open("output.wav", "wb") as f:
        f.write(bytes(audio_data))
    print("Audio saved as 'output.wav'.")
else:
    print(f"Error: {response.status_code}")


In [ ]:
from IPython.display import Audio

Audio("output.wav")
